# Data preperation 

The datasets from the IMDB database are normalised to atleast third degree, hence this notebook will take the the necassary fields of information and put it together for quick data retreival. This is essential as we want our system to be as quick as possible.

In [153]:
##importing libraries
import pandas as pd #for data manipulation
import unidecode #to replace accents with english letters

## Creating dataframe with Movie/Show information

### 1. Starting with main title file with language information

In [154]:
#reading the title files
df = pd.read_csv('../datasets from IMDB/title_akas.tsv',sep='\t')

/Users/shashanksharma/opt/anaconda3/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3058: DtypeWarning: Columns (7) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [155]:
df.head()

titleId  ordering                      title region language  \
0  tt0000001         1                 Карменсіта     UA       \N   
1  tt0000001         2                 Carmencita     DE       \N   
2  tt0000001         3  Carmencita - spanyol tánc     HU       \N   
3  tt0000001         4                 Καρμενσίτα     GR       \N   
4  tt0000001         5                 Карменсита     RU       \N   

         types     attributes isOriginalTitle  
0  imdbDisplay             \N               0  
1           \N  literal title               0  
2  imdbDisplay             \N               0  
3  imdbDisplay             \N               0  
4  imdbDisplay             \N               0

In [156]:
df.language.unique()

array(['\\N', 'ja', 'sv', 'en', 'tr', 'es', 'sr', 'cs', 'fa', 'fr', 'bg',
       'ca', 'nl', 'qbn', 'pt', 'ru', 'uk', 'qbp', 'ar', 'cmn', 'rn',
       'bs', 'de', 'hi', 'yi', 'qbo', 'ka', 'hr', 'sl', 'he', 'tg', 'sk',
       'kk', 'da', 'el', 'fi', 'it', 'gsw', 'yue', 'az', 'ms', 'pl', 'mr',
       'uz', 'gl', 'th', 'ta', 'eu', 'be', 'af', 'la', 'hy', 'ur', 'bn',
       'te', 'lt', 'mk', 'et', 'lv', 'gd', 'tl', 'cy', 'id', 'qal', 'gu',
       'ml', 'ro', 'hu', 'pa', 'kn', 'wo', 'no', 'is', 'sq', 'zh', 'ps',
       'nqo', 'sd', 'ga', 'xh', 'mi', 'zu', 'ku', 'rm', 'prs', 'ky', 'vi',
       'fro', 'ko', 'haw', 'mn', 'lo', 'my', 'am', 'qac', 'ne', 'myv',
       'br', 'iu', 'st', 'tn', 'cr'], dtype=object)

As observed above there are movies/shows from multiple languages in IMDB database. But, this project is only focussing on English and Hindi movies. Hence, rows of information for all other languages are removed

In [157]:
#Keeping titles with english or hindi titles and removing every other row of information
selected_languages=['en','hi']
df = df[df.language.isin(selected_languages)]

Also, columns like ordering,region, type, attributes and isOriginalTitle are of no use to the recommendation system. Hence, these columns are removed below.

In [158]:
df = df.drop(labels=['types','attributes','isOriginalTitle','ordering'],axis=1)

In [159]:
df.head()

titleId                                title region language
95   tt0000012               The Arrival of a Train    XWW       en
97   tt0000012  The Arrival of a Train at La Ciotat    XWW       en
107  tt0000012               The Arrival of a Train    XEU       en
157  tt0000016                Boat Leaving the Port    XWW       en
239  tt0000029                          Baby's Meal    XWW       en

### 2. Adding genre, year and title type(movie or show) information

In [160]:
#reading the file with basic title information 
basic = pd.read_csv('../datasets from IMDB/title_basics.tsv',sep='\t')

/Users/shashanksharma/opt/anaconda3/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3058: DtypeWarning: Columns (5) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [161]:
basic.head()

tconst titleType            primaryTitle           originalTitle  \
0  tt0000001     short              Carmencita              Carmencita   
1  tt0000002     short  Le clown et ses chiens  Le clown et ses chiens   
2  tt0000003     short          Pauvre Pierrot          Pauvre Pierrot   
3  tt0000004     short             Un bon bock             Un bon bock   
4  tt0000005     short        Blacksmith Scene        Blacksmith Scene   

   isAdult startYear endYear runtimeMinutes                    genres  
0        0      1894      \N              1         Documentary,Short  
1        0      1892      \N              5           Animation,Short  
2        0      1892      \N              4  Animation,Comedy,Romance  
3        0      1892      \N             12           Animation,Short  
4        0      1893      \N              1              Comedy,Short

Next, the basic data is joined with the title information. 

In [162]:
#joining the required columns from the the basic tile dataframe
basic = basic.set_index('tconst')
df_with_basic = pd.merge(df,basic[['titleType','isAdult','startYear','genres']],left_on='titleId',right_on='tconst',how='left')

In [163]:
df_with_basic.head()

titleId                                title region language titleType  \
0  tt0000012               The Arrival of a Train    XWW       en     short   
1  tt0000012  The Arrival of a Train at La Ciotat    XWW       en     short   
2  tt0000012               The Arrival of a Train    XEU       en     short   
3  tt0000016                Boat Leaving the Port    XWW       en     short   
4  tt0000029                          Baby's Meal    XWW       en     short   

   isAdult startYear                    genres  
0      0.0      1896  Action,Documentary,Short  
1      0.0      1896  Action,Documentary,Short  
2      0.0      1896  Action,Documentary,Short  
3      0.0      1895         Documentary,Short  
4      0.0      1895         Documentary,Short

Checking the types of titles in the data

In [164]:
df_with_basic.titleType.unique()

array(['short', 'movie', 'tvSeries', 'tvMovie', 'tvMiniSeries',
       'tvEpisode', 'tvShort', 'video', 'videoGame', 'tvSpecial', nan],
      dtype=object)

Only movies, tvSeries and TVMiniSeries are relavent to this project. Hence, every row of information with other title type is removed.

In [165]:
to_keep = ['movie','tvSeries','tvMiniSeries']
df_with_basic = df_with_basic[df_with_basic['titleType'].isin(to_keep)]

Checking the genres column for values.

In [166]:
df_with_basic.genres.unique()

array(['\\N', 'Drama', 'Drama,Romance', ...,
       'Musical,Reality-TV,Talk-Show', 'Comedy,Short,Talk-Show',
       'Music,Musical,Reality-TV'], dtype=object)

In [167]:
df_with_basic[df_with_basic.genres == '\\N']

titleId                                             title region  \
68       tt0000838                 The Cultivation of the Cacao Tree    XWW   
78       tt0001051                                     Magical Dream    XWW   
80       tt0001122                                       The Red Inn    XWW   
112      tt0002329                                Today and Tomorrow    XWW   
126      tt0002801                                 The Black Diamond    XWW   
...            ...                                               ...    ...   
2651813  tt9908394                            Sex Documentary: Meaty    XWW   
2651969  tt9909276               Documentary Porn: Compulsive Rapist    XWW   
2651992  tt9909736  Porno Documentary: Housewife's Prostitution Team    XWW   
2651993  tt9909744                 Please Seduce Me with Dirty Words    XWW   
2653017  tt9912812                                           Silence    XWW   

        language titleType  isAdult startYear genres  
68            en     movie      0.0      1909     \N  
78            en     movie      0.0      1909     \N  
80            en     movie      0.0      1910     \N  
112           en     movie      0.0      1912     \N  
126           en     movie      0.0      1913     \N  
...          ...       ...      ...       ...    ...  
2651813       en     movie      0.0      1981     \N  
2651969       en     movie      0.0      1981     \N  
2651992       en     movie      0.0      1981     \N  
2651993       en     movie      0.0      1981     \N  
2653017       en     movie      0.0      1991     \N  

[9105 rows x 8 columns]

Movie without genres ar of no use to this project. Hence they are removed.

In [168]:
#removing rows with \N as a genre
df_with_basic = df_with_basic[~(df_with_basic.genres =='\\N')]

Some english movie are mentioned twice in the dataste both in Hindi and English languages. This could have happened as english movies are often dubbed in hindi to reach to a wider audience. One such example is shown below

In [169]:
df_with_basic[df_with_basic.title == 'Coffee & Kareem']

titleId            title region language titleType  isAdult  \
2649423  tt9898858  Coffee & Kareem     CA       en     movie      0.0   
2649424  tt9898858  Coffee & Kareem     IN       hi     movie      0.0   

        startYear         genres  
2649423      2020  Action,Comedy  
2649424      2020  Action,Comedy

Checking if there are some movie in hindi woth region different to India.

In [170]:
df_with_basic[(df_with_basic.region != 'IN') & (df_with_basic.language == 'hi')]

titleId               title region language titleType  isAdult  \
21192    tt0085743  Jaane Bhi Do Yaaro     US       hi     movie      0.0   
2483062  tt9248934          Marjaavaan     CA       hi     movie      0.0   

        startYear                genres  
21192        1983          Comedy,Drama  
2483062      2019  Action,Drama,Romance

Changing the region of above title to India

In [171]:
df_with_basic.loc[(df_with_basic.title == 'Jaane Bhi Do Yaaro'),'region']='IN'
df_with_basic.loc[(df_with_basic.title == 'Marjaavaan'),'region']='IN'

Checking titles with region as India and language as english

In [172]:
df_with_basic[(df_with_basic.region == 'IN') & (df_with_basic.language == 'en')].tail(4000)


titleId                                              title region  \
843703    tt1210819                                    The Lone Ranger     IN   
846501    tt1211837                                     Doctor Strange     IN   
846961    tt1211956                                        Escape Plan     IN   
847493    tt1212142                                  Rowdy Gari Pellam     IN   
848750   tt12125238                                       Ek Thi Begum     IN   
850344    tt1212974                                         Bitch Slap     IN   
851239    tt1213404                                       Knight Rider     IN   
859903    tt1216496                                              Madeo     IN   
859968    tt1216520                                               Womb     IN   
862975   tt12176398                               Cooked with Cannabis     IN   
864812    tt1218345                    Untitled Shailesh Singh Project     IN   
866606    tt1219024                                             Castle     IN   
866738   tt12190580                                         Lenox Hill     IN   
867364    tt1219289                                          Limitless     IN   
867535    tt1219827                                 Ghost in the Shell     IN   
867671    tt1220214                                          Heartless     IN   
867843    tt1220617                                   The Inbetweeners     IN   
868157    tt1221133                           Easy Monthly Installment     IN   
868917    tt1223922                                               Blue     IN   
869989    tt1226271                                  The Damned United     IN   
870139    tt1226753                                           The Debt     IN   
870145    tt1226837                                      Beautiful Boy     IN   
870958    tt1228705                                         Iron Man 2     IN   
870982    tt1228933                                       Laid to Rest     IN   
870983    tt1228953                                            Big Fan     IN   
871124    tt1229413                                               Hung     IN   
871401    tt1230448                                       Billu Barber     IN   
872387    tt1232825                    Yi Ban Hai Shui, Yi Ban Huo Yan     IN   
872559    tt1233301                                           Ironclad     IN   
873026    tt1234719                                           Red Dawn     IN   
873132    tt1235099                                          Lie to Me     IN   
873933    tt1237373                                           Disarmed     IN   
874562    tt1239156                               Sunday NFL Countdown     IN   
875412    tt1241325                                        Objectified     IN   
875900    tt1242432                               I Spit on Your Grave     IN   
875914    tt1242530                                What's Your Zodiac?     IN   
876500    tt1243957                                        The Tourist     IN   
876956    tt1245492                                    This Is the End     IN   
877000    tt1245872           Magic's Biggest Secrets Finally Revealed     IN   
877756    tt1247704                                   Women in Trouble     IN   
878209    tt1248983                     The Relationship Is Up to Ooty     IN   
879091    tt1250777                                           Kick-Ass     IN   
880188    tt1253578                         A Matter of Life and Death     IN   
880260    tt1253864                                          Immortals     IN   
881744    tt1258189                                          Survivors     IN   
881746    tt1258197                                               Exam     IN   
881927    tt1258972                        The Man with the Iron Fists     IN   
882061    tt1259571                        The Twilight Saga: New Moon     IN   
883064    tt1262416                        

Changing language of titles with region in India to hindi

In [173]:
to_hindi = ['Baiju Bawra','Devdas','Pyaasa','Madhumati','Apur Sansar','Mughal-E-Azam','Dil Hi to Hai','Mahanagar','Kashmir Ki Kali','Mahapurush','Sadhu Aur Shaitaan','Amar Prem','Andaaz','Abhimaan','Bobby','Saudagar','Benaam','Majboor','Muqaddar Ka Sikandar','Sparsh','Chakra','Ram Balram','Taxi Chor','Naseeb','Namak Halaal','Satte Pe Satta','Andhaa Kaanoon','Sharabi','Ghulami','Mohabbat','Aakhree Raasta','Ijaazat','Awara Baap','Jalwa','Jawab Hum Denge','Salaam Bombay!','Batwara','Lamhe','Sanam Bewafa','Shivaji Surathkal','One Two Three','Agnisakshi','Sakhi Tumi Kar','Taj Mahal 1989','Kehta Hai Yeh Dil','Dosti Ka Naya Maidan','Kambakkht Ishq','Aswathama','Meri Gudiya','Amaanat','Mahabharatham','Kavita Bhabhi','Yehh Jadu Hai Jinn Ka','3 Shyaane','Chhaliya','Agra','Savdhaan India 3 - India Fights Back','Shubharambh','Phir Laut Aayi Naagin','Thappad','Hurdang','Bhoomi','Radhe','Dostana 2','K.G.F: Chapter 2','Sindura Bindu','Badnaam Gali','Hum Toh Tere Aashiq Hai','Naqaab','Awarapan','Race','Inkaar','Baarish','Love Aaj Kal','Dhol','Jeena Isi Ka Naam Hai','Om Namah Shivay','Kya Hoga Nimmo Ka','Kasamh Se',"Mani Ratnam's Guru",'Deal or No Deal','Pyaar Ke Side Effects','Sivaji: The Boss','Satyaghath: Crime Never Pays','Khosla Ka Ghosla!','Chalte Chalte Kahan Aagaye Hum','Lage Raho Munna Bhai','Chandramukhi','Lucky','Meri Jung: One Man Army','Deewane Huye Paaga','Mumbai Express','Parineeta','Zabaan Sambhal Ke','Afsana Dilwalon Ka','Phir Bhi Dil Hai Hindustani','Sanskar','Vikram Aur Betaal','Aap Ki Adalat','Tu Tu Main Main','Shaktimaan: The First Indian Superhero','Ramayan','Chandrakanta','Buniyaad','Meri Aan Man At Work','Tere Naam','Hungama','Kohraam','Karishma Kali Kaa','Ek Aur Ek Gyarah','Sakshyam','Mahatma','Lahore','Ek Hasina Thi','Krantikari','Saathiya','Yeh Dil Aashiqanaa','Ittefaq','Yeh Jo Hai Zindagi','Aarzoo','Shri Krishna','Hamara Dil Aapke Paas Hai','Saajan Chale Sasural','Tenali Rama','Phir Bhi Dil Hai Hindustani','Shola Aur Shabnam','Billu Barber','Firaaq','Don 2','Wake Up Sid','Kahaani Ghar Ghar Kii','Once Upon a Time in Bombay','StreetDance 3D','Kasautii Zindagii Kay','Kahiin to Hoga','Anjaana Anjaani','Paan Singh Tomar','Yamla Pagla Deewana','Kismat','Once Upon a Time in Mumbaai Again','Murder 2','Sasural Simar Ka','Matru Ki Bijlee Ka Mandola','Y.J.H.D.','Aashiqui 2','Shootout at Wadala','Singham Returns','Jannat 2','A.B.C.D','Gully Boy','Savdhaan India','Comedy Circus Ke Ajoobe','Kahani Comedy Circus Ki','Love Marriage Ya Arranged Marriage','Kuch Toh Log Kahenge','F.I.R.','Ninja Hattori','Tere Mere Sapne','Madhubala - Ek Ishq Ek Junoon','Jaanu','Yeh Hai Mohabbatein','Hum Saath Aath Hai','Humpty Sharma Ki Dulhania','Dishoom','The Shaukeens','Welcome to Karachi','Yeh Hai Aashiqui','Akbar Birbal','MTV Roadies','Bhabi Ji Ghar Par Hai','On Air with AIB','Meri Pyaari Bindu','Aahat','MTV Unplugged India','Yamla Pagla Deewana Again',"TSP's Zeroes",'Salaam Zindagi','Street Dancer 3D']

In [174]:
remove= ['Munnabhai 2nd Innings','Munnabhai 2nd Innings']

Changing language of the above title to hindi

In [175]:
df_with_basic.loc[(df_with_basic.title.isin(to_hindi)),'language']='hi'

In [176]:
df_with_basic = df_with_basic[~(df_with_basic.language.isin(remove))]

In [178]:
pd.set_option('display.max_rows', 4100)

In [181]:
df_with_basic[(df_with_basic.language == 'hi')].head(4060)

titleId                                              title region  \
543       tt0015324                                       Sherlock Jr.     IN   
1044      tt0021282                                      Rain or Shine     IN   
1139      tt0022268                                    Platinum Blonde     IN   
1235      tt0023464                                           Shopworn     IN   
1315      tt0024617                          The Story of Temple Drake     IN   
1531      tt0027817                                       Jeevan Naiya     IN   
1544      tt0027977                                       Modern Times     IN   
1562      tt0028212                                           Sabotage     IN   
1993      tt0033029                                      Second Chorus     IN   
2278      tt0035209                                     Prelude to War     IN   
2283      tt0035241                                               Race    XWW   
2524      tt0037120                                    National Velvet     IN   
2533      tt0037174                                              Phool     IN   
2542      tt0037213                                             Rattan     IN   
2571      tt0037412                                        Udahir Path     IN   
2617      tt0037611                                           Conflict     IN   
2624      tt0037629                                     The Ghost Lady     IN   
2719      tt0038268                          Sanshiro Sugata, Part Two     IN   
2852      tt0038931                                          Shahjehan     IN   
2959      tt0039322                                        Dil Ki Rani     IN   
2998      tt0039431                                          Good News     IN   
3078      tt0039776                                        Road to Rio     IN   
3238      tt0040418                                       Port of Call     IN   
3311      tt0040724                                          Red River     IN   
3331      tt0040761                             Scott of the Antarctic     IN   
3751      tt0042207                                             Aarzoo     IN   
3813      tt0042380                                            Dastaan     IN   
3997      tt0042876                                           Rashomon     IN   
4141      tt0043306                                              Awara     IN   
4143      tt0043310                                              Bahar     IN   
4512      tt0044392                                        Baiju Bawra     IN   
4562      tt0044527                                              Daagh     IN   
4756      tt0045094                                       Road to Bali     IN   
4831      tt0045467                                               Aah!     IN   
5080      tt0046155                                              Paapi     IN   
5086      tt0046164                                          Parineeta     IN   
5279      tt0046791                                        Black Widow     IN   
5282      tt0046799                                        Boot Polish     IN   
5401      tt0047110                                             Ilzaam     IN   
5450      tt0047271                                             Naukri     IN   
5517      tt0047478                                      Seven Samurai     IN   
5676      tt0047990                                             Devdas     IN   
5733      tt0048181                                     Ghar Number 44     IN   
5916      tt0048613                                           Shri 420     IN   
5964      tt0048756                                      Udaan Khatola     IN   
5965      tt0048756                                       Udan Khatola     IN   
6009      tt0048951                                         Delhi Mein     IN   
6010      tt0048951                                             Anjaan     IN   
6011      tt0048951                        

In [184]:
to_english = ['Sherlock Jr.','Rain or Shine','Platinum Blonde','Shopworn','Black Widow','Seven Samurai','12 Angry Men','Witness for the Prosecution','Hiroshima Mon Amour','Psycho',"Cleopatra's Daughter",'The Good, the Bad and the Ugly',"Guess Who's Coming to Dinner",'The Nude Restaurant','Point Blank','Enter the Game of Death','Marlowe','The Love Factor','Days and Nights in the Forest','Hollywood Blue','Murmur of the Heart','Enter the Dragon','Belladonna of Sadness','The Godfather: Part II','The Holy Mountain','The Night Porter','The Story of O','Submission','Star Wars: Episode IV - A New Hope','Apocalypse Now','American Gigolo','The Blue Lagoon','Caligula','Star Wars: Episode V - The Empire Strikes Back','Superman II','The Shining','The Entity','Private Lessons','Reds','Basket Case','Caligula and Messalina','E.T. the Extra-Terrestrial','The Evil Dead','A Little Sex','Outsiders','Star Wars: Episode VI - Return of the Jedi','Scarface','Trading Places','Gremlins','Angel','Hollywood Hot Tubs','The Terminator','Dragon Ball','Back to the Future','The Goonies','Little Flames','The Mosquito Coast','9½ Weeks','Top Gun','Stand by Me','Welcome to 18','Star Trek: The Next Generation','What Every Frenchwoman Wants','Full Metal Jacket','The Lost Boys','The Untouchables','Grave of the Fireflies','Legend of the Galactic Heroes','Wild Orchid','The Marrying Man','Only Yesterday','The Silence of the Lambs','Basic Instinct','Dracula','All Ladies Do It','he Opposite Sex and How to Live with Them','Reservoir Dogs','Scent of a Woman','Tokyo Decadence','Bad Boy Bubby','Jurassic Park',"Schindler's List",'Naked',"Baby's Day Out",'Friends','Cold Water','Forrest Gump','The Lion King','The Professional','The Shawshank Redemption','Pulp Fiction','The Smile of the Fox','Bad Boys','Braveheart','The Wood','Cast Away','American Pie','The Lord of the Rings: The Return of the King','The Sixth Sense','Boredom','American Beauty','The White Ship','Siska','Frivolous Lola','Golden Eyes Secret Agent 077','Requiem for a Dream','Little Nicky','Romance','Schoolgirls in Chains','Bionic Ninja','Wolf Guy','Sexy','Sexy Beast','Paths in the Night','Naked Video','Snatch','Memento','Amélie','Love & Sex','The Matrix Revolutions','Spirited Away','AMALL','The Pianist','Sex and Lucia','The Pornographer','Catch Me If You Can','The Girl Next Door','Battle Royale','Hollywood Sex Fantasy','Kill Bill: Vol. 1','Black Angel',"People's Dada","Red Dragon",'Meet the Fockers','X2: X-Men United','The Office','800 Bullets','Wrong Turn','xXx','Take Care of My Cat','Shrek 2','Timeline','Sex Is Comedy','The Wire','City of God','Berserk','Big Fish','The Day After Tomorrow','The Day Maradona Met Gardel','Pirates of the Caribbean: The Curse of the Blacl Pearl','The Best Sex Ever',"I'm Not Scared",'Mystic River','The Stepford Wives','Ella Enchanted','xXx: State of the Union','Scooby-Doo 2: Monsters Unleashed','The Notebook','Eternal Sunshine of the Spotless Mind','The Haunted Mansion','The Polar Express','Two Brothers','The Aviator','I, Robot','Memories of Murder','King Kong','Inglourious Basterds','The Life Aquatic with Steve Zissou','Downfall','The Chronicles of Narnia: The Lion, the Witch and the Wardrobe','Taking Lives','Please Teacher!','Charlie and the Chocolate Factory','D.E.B.S.','Jurassic World','Iron Man','Batman Begins','Saints and Soldiers','The Story of the Weeping Came','Halloween','Mi piace lavorare (Mobbing)','Jack Paradise (Les nuits de Montréal)','Crash','Survival Island','The Criminals','The Ellen DeGeneres Show','The 7th Day','Casino Royale','Ma Mère','The Da Vinci Code','Ratatouille','Rome','Motherless Brooklyn','The Office','The Grudge','The Exorcism of Emily Rose','Little Children','Casshern','The Departed','Watchmen','Lost','9 Songs','House M.D.','Veronica Mars','Spider-Man 3',"Grey's Anatomy",'Show Me Yours','300','Avatar: The Last Airbender','Land of the Dead','Lie with Me','A Soap','Fullmetal Alchemist','The Curious Case of Benjamin Button','V for Vendetta','The Invisible','Kidulthood','Next','Doctor Who','Alita: Battle Ange','Angel','Beowulf','Zodiac','The Painted Veil','Shazam!','Hancock','Blood Diamond','Wonder Woman','Good Luck Chuck','Lady in the Water','Perfect Mismatch','Life of Pi','The Equalizer','The Smart Hunt','Prison Break','Reincarnation','The Holiday','Star Wars: The Clone Wars','Captain America: The First Avenger','X-Men Origins: Wolverine','How I Met Your Mother','Supernatural','Spanish Beauty','The Prince of Tennis','Unnatural & Accidental','The Dark Knight','There Will Be Blood','Eagle Man','Apocalypto',"It's Always Sunny in Philadelphia",'Robbery','Westworld','Big Brother','No Country for Old Men','I Am Legend','A Good Day to Be Black & Sexy','The Prestige','Bus Conductor','The Ode to Joy','Fantastic 4: Rise of the Silver Surfer','Miss Cobra','XXXHOLiC','The Oxford Murders','Good Boy, Bad Boy','Carnival Row','Sixty Six','Strictly Sexual','Our Victory','Time','Into the Wild','Body of Lies','The Tudors','Man of Steel','Dexter',"My Mom's New Boyfriend",'Getting Home','The Last Full Measure','Honeymoon','Meet Bill','Flood','Carriers','Interstellar','World War Z','The Sex Movie','Arn: The Knight Templar','Pet Sematary','The Town','The Avengers','Death Note','The Big Bang Theory','The Hobbit: An Unexpected Journey','Breaking Bad','Young People Fucking','Harry Potter and the Deathly Hallows: Part 1','Salt','Game of Thrones','Source Code','Black Swan','The Amazing Spider-Man','The Happening','Six Sex Scenes and a Murder','Sherlock Holmes','The Wolf of Wall Street','The Struggle','Sex Drugs & Theatre','Medically Yourrs',"Hellcat's Revenge II: Deadman's Hand",'The Gift','Sweater','Under the Blue Sky','The Secret Life of My Secretary',"Angel's Last Mission: Love",'Sing "Yesterday" for Me','Never Back Down','Avenue 5','Argo','Sleeping with My Student','Death Proof',"Hachi: A Dog's Tale",'Bluff City Law','Stumptown','Outmatched','Prodigal Son','All Rise','You Cannot Hide','Fly Girls','Titans','Mission Over Mars','Black Christmas','Stalked','Bad Guys: The Movie','They Say Nothing Stays the Same',"Inside Bill's Brain: Decoding Bill Gates",'The Hole','House Arrest','Cosmos: Possible Worlds','Shutter Island','Sex Drive','Cubicles','Coloquinte','The Kung Fu Master','Handsome Siblings','Zombieland','Spice and Wolf','Little Soldier','The Rite','Never Kiss Your Best Friend','The Hobbit: The Desolation of Smaug','Wuthering Heights','7 Islands','The Boys','Memorist','The Mentalist','Harry Potter and the Deathly Hallows: Part 2','Gran Torino','The Rebound','Jack Ryan: Shadow Recruit','Rambo: Last Blood','Moneyball','Doctor Strange','I Am Love','Mission: Impossible - Ghost Protocol','Sorority Row',"Don't Look Down",'Conviction','Sex and the City 2','Room in Rome','X-Men: First Class','A Serbian Film','The Social Network','Bad Teacher','Sex Ed','xXx: Return of Xander Cage','Pirates of the Caribbean: On Stranger Tides','The Irishman','The Secret in Their Eyes','The Twilight Saga: Breaking Dawn: Part 1','3-D Sex and Zen: Extreme Ecstasy','Tomb Raider','Suicide Squad','Mad Max: Fury Road','42 Kilometres','Journey 2: The Mysterious Island','No Strings Attached','Apartment: Are You Looking for One?','X-Man Wolverine 2','The Conjuring','Gravity','Sherlock','Aquaman','Oblivion','Bad Boys for Life','The Walking Dead','Point Blank','Zombieland: Double Tap','Maleficent','Suits','Friends with Benefits','Maid Sama!','Project X','The Dictator','The Impossible','X: Night of Vengeance','This Is Not a Film','Now You See Me','The Twilight Saga: Breaking Dawn - Part 2','Intouchables','Trollhunters: Tales of Arcadia','Top Gun: Maverick','Orchids: My Intersex Adventure','Hollywood Sex Wars','Hollywood Sex Wars','Is This a Zombie?','Pirates of the Caribbean: Dead Men Tell No Tales','Black & White & Sex','Prosecutor Princess','13 Reasons Why','Person of Interest','American Horror Story','Django Unchained','House of Cards','Blade Runner 2049','Hollywood Rules','The World God Only Knows',"Let's Be Cops","Miss Peregrine's Home for Peculiar Children",'The Hangover Part III','Toy Story 4','Rush','Angry Birds','A Aa E Ee','Guardians of the Galaxy','The Great Wall','Ip Man 4: The Finale','The Imitation Game','Black Mirror','Inside Out','The Hunt','The Queen of Versailles','A Boy Called Sailboat','True Story','Men in Black: International','Naruto SD: Rock Lee & His Ninja Pals','The Hobbit: The Battle of the Five Armies','Fifty Shades of Grey','Avengers: Age of Ultron','Cosmos: A Spacetime Odyssey','Predestination','Outlawed','Star Wars: The Rise of Skywalker','Silicon Valley','The Town That Dreaded Sundown','The Fault in Our Stars','Whiplash','Me Before You','Narcos','The Blacklist','Bad Man','The Interview','Kingsman: The Secret Service','Furious 7','Ip Man 3','Shank','John Wick','Insurgent','The Jungle Book','Now You See Me 2','Into the Ashes','I Hear Your Voice','The Nightmare','The Boy Next Door',"Master's Sun",'Palm Trees in the Snow','Nine: Nine Time Travels',"I Do... Until I Don't",'Sully','Obsessed','Logan','Zapatlela 2','Daredevil','Heartless','Transformers: The Last Knight','X-Men: Apocalypse','When Marnie Was There','Despicable Me 3','The Hateful Eight','My Love from the Star']

In [183]:
remove_eng = ['Léon: The Professional','KKHH','****','KNPH','K3G','KKKG','www.XXX.com','R.D.B.','Veer-Zaara','Koi... Tumsa Nahin','Perfect Mis Match','Munnabhai 2nd Innings','Don: The Chase Begins Again','Dashavtar','Sivaji',"Mani Ratnam's Guru",'Harry Potter aur maut ke tohfe, part 1','XXY','Search: WWW','www.love.com','Love.Com','Guardians of the Galaxy: Anktriksh ke Boss','A.B.C.D','Cosmos','Furious Seven']

Now, there are reptetition of titles as seen below. To keep the right data, 
* The region of every title from US or Canada will be changed to AA
* The region of every title from India stays as it is
* The region of every title with any other country/region changes to ZZ

We will now sort the rows in descending order of langugae and region. The duplicated that will occur first are kept and everything else is removed.


In [75]:
df_with_basic[df_with_basic.duplicated(subset=['title'], keep=False)]

titleId                  title region language titleType  isAdult  \
73       tt0000941             Love Crazy    XWW       en     movie      0.0   
82       tt0001175                Camille    XWW       en     movie      0.0   
127      tt0002844               Fantomas    XWW       en     movie      0.0   
150      tt0003419  The Student of Prague    XWW       en     movie      0.0   
153      tt0003622      Love of Perdition    XWW       en     movie      0.0   
...            ...                    ...    ...      ...       ...      ...   
2649644  tt9900908              Handcuffs    XWW       en     movie      0.0   
2651088  tt9906644              Manoharam     CA       en     movie      0.0   
2651089  tt9906644              Manoharam     IN       hi     movie      0.0   
2653686  tt9915686   Khatra Khatra Khatra     IN       hi  tvSeries      0.0   
2653688  tt9915686   Khatra Khatra Khatra     IN       en  tvSeries      0.0   

        startYear                genres  
73           1909                 Drama  
82           1912         Drama,Romance  
127          1913           Crime,Drama  
150          1913  Drama,Fantasy,Horror  
153          1914                 Drama  
...           ...                   ...  
2649644      1969   Action,Comedy,Crime  
2651088      2019          Comedy,Drama  
2651089      2019          Comedy,Drama  
2653686      2019     Comedy,Reality-TV  
2653688      2019     Comedy,Reality-TV  

[36028 rows x 8 columns]

Changing region of othr countires to ZZ

In [76]:
index = (df_with_basic.language == 'en') & ((df_with_basic.region != 'US') | (df_with_basic.region != 'CA'))
df_with_basic.loc[(index),'region']='ZZ'

In [77]:
df_with_basic[(df_with_basic.language == 'en') ]

titleId                                 title region language  \
73       tt0000941                            Love Crazy     ZZ       en   
82       tt0001175                               Camille     ZZ       en   
86       tt0001258                 The White Slave Trade     ZZ       en   
88       tt0001338                        A Night in May     ZZ       en   
93       tt0001790  Les Misérables, Part 1: Jean Valjean     ZZ       en   
...            ...                                   ...    ...      ...   
2653687  tt9915686                       The Khatra Show     ZZ       en   
2653688  tt9915686                  Khatra Khatra Khatra     ZZ       en   
2653746  tt9916170                         The Rehearsal     ZZ       en   
2653749  tt9916206                                 Nojor     ZZ       en   
2653751  tt9916216          Kalyanam Mudhal Kadhal Varai     ZZ       en   

        titleType  isAdult startYear             genres  
73          movie      0.0      1909              Drama  
82          movie      0.0      1912      Drama,Romance  
86          movie      0.0      1910              Drama  
88          movie      0.0      1910              Drama  
93          movie      0.0      1913              Drama  
...           ...      ...       ...                ...  
2653687  tvSeries      0.0      2019  Comedy,Reality-TV  
2653688  tvSeries      0.0      2019  Comedy,Reality-TV  
2653746     movie      0.0      2019              Drama  
2653749  tvSeries      0.0      2019            Fantasy  
2653751  tvSeries      0.0      2014            Romance  

[122779 rows x 8 columns]

In [78]:
#Sorting the dataframe by langauge column
df_with_basic.sort_values(by=['region','language'],ascending= False ,inplace=True)

In [79]:
df_with_basic.drop_duplicates(subset=['titleId'],keep='first',inplace=True)

Checking again.

In [80]:
#checking again to confirm that Coffee & Kareem only appears in Enlglish language
df_with_basic[df_with_basic.title == 'Coffee & Kareem']

titleId            title region language titleType  isAdult  \
2649423  tt9898858  Coffee & Kareem     ZZ       en     movie      0.0   

        startYear         genres  
2649423      2020  Action,Comedy

The language is correct now. Let's add ratings to the datframe now.

### 3.  Adding ratings information

In [81]:
ratings = pd.read_csv('../datasets from IMDB/title_rating.tsv',sep='\t')

In [82]:
ratings.head()

tconst  averageRating  numVotes
0  tt0000001            5.6      1608
1  tt0000002            6.0       197
2  tt0000003            6.5      1286
3  tt0000004            6.1       121
4  tt0000005            6.1      2051

Joining the ratings information with the dataframe created above.

In [83]:
ratings = ratings.set_index('tconst')
df_with_ratings = pd.merge(df_with_basic,ratings,left_on='titleId',right_on='tconst',how='left')

In [84]:
df_with_ratings.head()

titleId                                 title region language titleType  \
0  tt0000941                            Love Crazy     ZZ       en     movie   
1  tt0001175                               Camille     ZZ       en     movie   
2  tt0001258                 The White Slave Trade     ZZ       en     movie   
3  tt0001338                        A Night in May     ZZ       en     movie   
4  tt0001790  Les Misérables, Part 1: Jean Valjean     ZZ       en     movie   

   isAdult startYear         genres  averageRating  numVotes  
0      0.0      1909          Drama            4.2      13.0  
1      0.0      1912  Drama,Romance            5.5      22.0  
2      0.0      1910          Drama            5.8      80.0  
3      0.0      1910          Drama            5.4       7.0  
4      0.0      1913          Drama            5.8      21.0

In [85]:
df_with_ratings.shape

(99015, 10)

In [86]:
df_with_ratings['title'] = df_with_ratings['title'].apply(lambda x: unidecode.unidecode(x))

In [87]:
df_with_ratings = df_with_ratings[~(df_with_ratings.startYear =='\\N')]
df_with_ratings['startYear'] = df_with_ratings['startYear'].apply(int)
df_with_ratings =  df_with_ratings[df_with_ratings.startYear >= 1950]

In [88]:
df_with_ratings.startYear.min()

1950

In [89]:
df_with_ratings.dropna(axis=0,how='any',inplace=True)

In [90]:
df_with_ratings.shape

(73161, 10)

In [91]:
df_with_ratings.titleType.unique()

array(['movie', 'tvSeries', 'tvMiniSeries'], dtype=object)

In [92]:
df_with_ratings.loc[(df_with_ratings.titleType == 'tvMiniSeries'),'titleType']='Mini-Series'
df_with_ratings.loc[(df_with_ratings.titleType == 'tvSeries'),'titleType']='Series'

In [93]:
df_with_ratings.loc[(df_with_ratings.language == 'en'),'language']='English'
df_with_ratings.loc[(df_with_ratings.language == 'hi'),'language']='Hindi'

In [100]:
df_with_ratings[df_with_ratings.language == 'Hindi'].sample(50)

titleId                            title region language titleType  \
97768   tt0483786                    Ram Aur Shyam     IN    Hindi     movie   
98399   tt3322892                               XX     IN    Hindi     movie   
97308   tt0215987                         Dawedaar     IN    Hindi     movie   
97268   tt0175572                           Do Dil     IN    Hindi     movie   
98112   tt1606253                        Yes or No     IN    Hindi     movie   
98100   tt1586680                        Shameless     IN    Hindi    Series   
97298   tt0213611                      Dharam-Veer     IN    Hindi     movie   
97450   tt0272736             Mujhse Dosti Karoge!     IN    Hindi     movie   
98976   tt9448332                             Ishq     IN    Hindi     movie   
98672   tt6117702                    Munna Michael     IN    Hindi     movie   
98175   tt1840309                        Divergent     IN    Hindi     movie   
97934   tt1101665                          Shaurya     IN    Hindi     movie   
97296   tt0212812                     Dhyanu Bhakt     IN    Hindi     movie   
97349   tt0234530                           Abhaas     IN    Hindi     movie   
97561   tt0347278                    Jhankar Beats     IN    Hindi     movie   
98421   tt3557988                       Bhaigiri 2     IN    Hindi     movie   
98155   tt1760980                     Madrid, 1987     IN    Hindi     movie   
98905   tt8810990                             Kiss     IN    Hindi     movie   
98624   tt5607782                     The Covenant     IN    Hindi     movie   
97240   tt0105271                             Roja     IN    Hindi     movie   
97206   tt0084840                            Subah     IN    Hindi     movie   
97266   tt0174431                            Siska     IN    Hindi    Series   
98472   tt4103470                         Mistrust     IN    Hindi     movie   
98621   tt5583554                          Harmony     IN    Hindi     movie   
97449   tt0272062                  Daagh: The Fire     IN    Hindi     movie   
97939  tt11134856                Chhappad Phaad Ke     IN    Hindi     movie   
98119   tt1620719                          Dabangg     IN    Hindi     movie   
97426   tt0264464              Catch Me If You Can     IN    Hindi     movie   
98087   tt1575719                  Ek Aur Rajkumar     IN    Hindi     movie   
98159   tt1773042  Shahrukh Bola Khoobsurat Hai Tu     IN    Hindi     movie   
97865   tt1034431                     Rocky Bheema     IN    Hindi     movie   
98068   tt1483013                         Oblivion     IN    Hindi     movie   
99008   tt9789440             Veedani Needanu Nene     IN    Hindi     movie   
97304   tt0215457                           Byalis     IN    Hindi     movie   
98566   tt4995784                         RX Soori     IN    Hindi     movie   
98207   tt1995245   Aamras: Dosti Ka Meetha Ehsaas     IN    Hindi     movie   
98086   tt1575640              Sabse Bada Jungbaaz     IN    Hindi     movie   
97467   tt0279309                         Naag Lok     IN    Hindi     movie   
98477   tt4148838                             Mard     IN    Hindi     movie   
97860  tt10329042                         All Rise     IN    Hindi    Series   
97392   tt0250468                Killing Me Softly     IN    Hindi     movie   
98308   tt2714622                Dangerous Khiladi     IN    Hindi     movie   
98130   tt1646980                       The Double     IN    Hindi     movie   
98692   tt6275296         The Rules for Everything     IN    Hindi     movie   
98146   tt1740092      Chitkabrey - Shades of Grey     IN    Hindi     movie   
97986   tt1228744                          Pranali     IN    Hindi     movie   
98309   tt2714664     Love Story of Singh vs. Kaur     IN    Hindi     movie   
98617   tt5553436                   London Rampage     IN    Hindi     movie   
98010   tt1285301                          Awasthi     IN    Hindi     movie   
97815   tt

Creating a csv with title information

In [95]:
df_with_ratings.to_csv("title_information.csv")

## Creating dataframe with cast information for each title

### 1. Creating dataframe with actor, actress and director infromation

Reading principal actor info

In [42]:
cast_info = pd.read_csv('../datasets from IMDB/title_principal.tsv',sep='\t')

In [43]:
cast_info.head(20)

tconst  ordering     nconst         category                      job  \
0   tt0000001         1  nm1588970             self                       \N   
1   tt0000001         2  nm0005690         director                       \N   
2   tt0000001         3  nm0374658  cinematographer  director of photography   
3   tt0000002         1  nm0721526         director                       \N   
4   tt0000002         2  nm1335271         composer                       \N   
5   tt0000003         1  nm0721526         director                       \N   
6   tt0000003         2  nm5442194         producer                 producer   
7   tt0000003         3  nm1335271         composer                       \N   
8   tt0000003         4  nm5442200           editor                       \N   
9   tt0000004         1  nm0721526         director                       \N   
10  tt0000004         2  nm1335271         composer                       \N   
11  tt0000005         1  nm0443482            actor                       \N   
12  tt0000005         2  nm0653042            actor                       \N   
13  tt0000005         3  nm0005690         director                       \N   
14  tt0000005         4  nm0249379         producer                 producer   
15  tt0000006         1  nm0005690         director                       \N   
16  tt0000007         1  nm0179163            actor                       \N   
17  tt0000007         2  nm0183947            actor                       \N   
18  tt0000007         3  nm0005690         director                       \N   
19  tt0000007         4  nm0374658         director                       \N   

        characters  
0         ["Self"]  
1               \N  
2               \N  
3               \N  
4               \N  
5               \N  
6               \N  
7               \N  
8               \N  
9               \N  
10              \N  
11  ["Blacksmith"]  
12   ["Assistant"]  
13              \N  
14              \N  
15              \N  
16              \N  
17              \N  
18              \N  
19              \N

Removin titles in cast datafrme which are not present in the datafrme created above.

In [44]:
cast_info = cast_info[cast_info.tconst.isin(df_with_ratings.titleId)]

Keeping the inforamtion of actor, actress and director and removing everything else

In [45]:
cast_info = cast_info[(cast_info.category == 'actor') | (cast_info.category == 'actress') | (cast_info.category == 'director')]

Removing the columns which are not required for the project. 

In [46]:
cast_info.drop(labels=['ordering','job','characters'], axis=1,inplace=True)

In [47]:
cast_info.head()


tconst     nconst  category
316495  tt0039442  nm0007023     actor
316496  tt0039442  nm0544330   actress
316497  tt0039442  nm0019330     actor
316498  tt0039442  nm0370455   actress
316499  tt0039442  nm0349426  director

### 2. Replacing the codes for cast with their names

In [48]:
name_info = pd.read_csv('../datasets from IMDB/name_basics.tsv',sep='\t')

In [49]:
name_info.head()

nconst      primaryName birthYear deathYear  \
0  nm0000001     Fred Astaire      1899      1987   
1  nm0000002    Lauren Bacall      1924      2014   
2  nm0000003  Brigitte Bardot      1934        \N   
3  nm0000004     John Belushi      1949      1982   
4  nm0000005   Ingmar Bergman      1918      2007   

                primaryProfession                           knownForTitles  
0  soundtrack,actor,miscellaneous  tt0050419,tt0043044,tt0072308,tt0053137  
1              actress,soundtrack  tt0037382,tt0038355,tt0071877,tt0117057  
2     actress,soundtrack,producer  tt0059956,tt0049189,tt0054452,tt0057345  
3         actor,soundtrack,writer  tt0077975,tt0080455,tt0072562,tt0078723  
4           writer,director,actor  tt0083922,tt0050976,tt0050986,tt0060827

In [50]:
#replacing the codes in the cast dataframe from names
cast_info['nconst'] = cast_info['nconst'].map(name_info.set_index('nconst')['primaryName'])

In [51]:
#renaming names column
cast_info.rename(columns = {'nconst':'name'}, inplace = True)

In [52]:
cast_info.head()

tconst                     name  category
316495  tt0039442  José Luis López Vázquez     actor
316496  tt0039442              Kiti Mánver   actress
316497  tt0039442         Francisco Algora     actor
316498  tt0039442            Hanna Haxmann   actress
316499  tt0039442  Manuel Gutiérrez Aragón  director

Changing the values in name column to string and then replacing accents with unaccanted letters.

In [53]:
cast_info['name'] = cast_info['name'].apply(str)
cast_info['name'] = cast_info['name'].apply(lambda x: unidecode.unidecode(x))

Writing to csv file

In [54]:
cast_info = cast_info.reset_index()
cast_info.to_csv('cast_information.csv',encoding="UTF-8")